# 6. Splitting the valence/conduction of silicon

```@meta
CurrentModule = Wannier
```

In the previous tutorial, we have seen how to use the `parallel_transport` function
to automate the construction of WFs for isolated manifold.
In this tutorial, we will again use this technique, combined with disentanglement,
to Wannierize the valence and conduction manifolds of silicon, separately.

Usually, Wannierization of valence or conduction manifold is difficult because
there is no prior knowledge of the bonding or anti-bonding orbitals, except for
simple system.

For the valence manifold, since it is isolated, we can

- use random Gaussian as initial projections, then run many iterations of maxiaml localization,
- use SCDM for the isolated manifold, then run maximal localization.

However, for the conduction manifold, it is entangled with higher energy bands,
so the random Gaussian is not applicable. In such case, we can

- use SCDM with specified $\mu$ and $\sigma$ for the conduction manifold,
    then run maximal localization.

However, the quality of Wannierization sensitively depends on the $\mu$ and $\sigma$,
and also SCDM works in real space which is more memory consuming.

Now, our solution is

- run the normal disentanglement on valence + conduction manifold, the initial guess
    can be the analytic spdf projectors, or using numerical atomic orbitals (NAOs)
    from pseudopotentials (for plane-wave code like QE, this automates the initial
    projections for the disentanglement).
- separate the valence + conduction manifold into two, by diagonalizing the Wannier
    gauge Hamiltonian, the eigenvectors are unitary matrices, in which the upper (lower)
    part maps to the valence (conduction) manifold. Thus we have two separated submanifolds.
- run the `parallel_transport` on the separated submanifolds, to construct the
    parallel transport gauge (PTG) for valence and conduction, respectively.
    We can further run optimal rotation and maximal localization to smoothen the gauge.

The disentanglement generates a smooth "total" manifold, helping us getting rid of
higher energy states, and the PTG automates the gauge construction for the two separated
submanifolds. In final, we have an automated approach to Wannierize the valence and/or
conduction manifolds without human intervention.

## Outline

1. construct a `Model`, by reading the `win`, `amn`, `mmn`, and `eig` files
2. split the `Model` by diagonalizing the Wannier gauge Hamiltonian
3. run `parallel_transport` on the two `Model`s to construct PTG for valence
    and conduction, respectively
4. maxiaml localize to smoothen the PTG
5. interpolate band structures

!!! tip

    This is a HTML version of the tutorial, you can download corresponding
    - Jupyter notebook: [`tutorial.ipynb`](./tutorial.ipynb)
    - Julia script: [`tutorial.jl`](./tutorial.jl)

## Preparation
Load the package

In [ ]:
using Wannier
using WannierPlots

## Model generation

We will use the `read_w90` function to read the
`win`, `amn`, `mmn`, and `eig` files, and construct a `Model` that abstracts the calculation

In [ ]:
model = read_w90("si2")

## Disentanglement

First let's disentangle the valence + conduction manifold,

In [ ]:
U = disentangle(model);

## Splitting the model

Then we split the model into two, by diagonalizing the Wannier gauge Hamiltonian,
we need to pass it the number of valence bands, `n_val`,

In [ ]:
n_val = 4
(model_v, Uv), (model_c, Uc) = split_model(model, n_val)

Returned are two separated `Model`s, and the two corresponding gauge transformation
matrices from the total manifold to the two separated submanifolds.
This is useful if you want to further rotate the gauge of some operators,
or if you want to rotate the `UNK` files for plotting WFs,
in that case you need to pass these two matrices to the function
`split_unk`.

Next, we construct PTG for the two `Model`s,

In [ ]:
Uv, _ = parallel_transport(model_v)
model_v.U .= Uv;

and

In [ ]:
Uc, _ = parallel_transport(model_c)
model_c.U .= Uc;

and take a look at the spread

In [ ]:
omega(model_v)
omega(model_c)

!!! tip

    There is a `split_wannierize` function that combines the above steps,
    however, for pedagogical purpose we run them manually.

## Further maximal localization

We can further run maximal localization to smoothen the gauge,

In [ ]:
Uv = max_localize(model_v)
model_v.U .= Uv;

and

In [ ]:
Uc = max_localize(model_c)
model_c.U .= Uc;

!!! tip

    For such simple case (few bands, very little kpoints) a direct maximal localization
    is sufficient. But for more complex scenarios, running an `opt_rotate` might
    be helpful.

## Comparing spreads

The valence + conduction,

In [ ]:
model.U .= U;
omega(model)

the valence,

In [ ]:
omega(model_v)

the conduction,

In [ ]:
omega(model_c)

Look, we have well-localized WFs for all the three cases,
the initial 8 s,p orbitals are separated into 4 bonding
and 4 anti-bonding orbitals! 🚀

## Band structure

Finally, let's compare band interpolation,

In [ ]:
using PlotlyJS

the valence + conduction,

In [ ]:
interp_model = Wannier.InterpModel(model)
kpi, E = interpolate(interp_model)

the valence,

In [ ]:
interp_model_v = Wannier.InterpModel(model_v)
_, Ev = interpolate(interp_model_v)

the conduction,

In [ ]:
interp_model_c = Wannier.InterpModel(model_c)
_, Ec = interpolate(interp_model_c)

and compare valence,

In [ ]:
P = plot_band_diff(kpi, E, Ev)
Main.HTMLPlot(P, 500)  # hide

and conduction,

In [ ]:
P = plot_band_diff(kpi, E, Ec)
Main.HTMLPlot(P, 500)  # hide

!!! note

    Again, the interpolation quality is not good (especially for the conduction
    which has much larger spread WFs), bacause of the very coarse
    kgrid, increase the kgrid and compare the resulting band structures.

Bravo, we have successfully Wannierized the valence and conduction manifolds,
by splitting the gauge of a valence + conduction calculation!

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*